In [1]:
cd /home/jupyter/PACE

/home/jupyter/PACE


In [2]:
ls

Declarations_19722_Merge.shp.xml  data/
aoi_flood_footprint.geojson       notebooks/


# **Install & import packages**

In [3]:
!pip install git+https://github.com/spaceml-org/ml4floods#egg=ml4floods
!pip install pygeos

  Cloning https://github.com/spaceml-org/ml4floods to /tmp/pip-install-stlxyl_2/ml4floods_98669f4fa18c4615b54076b2de8b74c8
  Running command git clone --filter=blob:none --quiet https://github.com/spaceml-org/ml4floods /tmp/pip-install-stlxyl_2/ml4floods_98669f4fa18c4615b54076b2de8b74c8
  Resolved https://github.com/spaceml-org/ml4floods to commit 36d001bbb6ed85d09b4550304b01e9a03344f34f
  Preparing metadata (setup.py) ... done


In [90]:
import pandas as pd
import geopandas as gpd
import numpy as np
import os
import pygeos
gpd.options.use_pygeos = True

import ee
from ml4floods.data import ee_download
from datetime import datetime, timedelta, timezone
import geemap.eefolium as geemap
import folium

In [5]:
ee.Authenticate()
ee.Initialize()

Enter verification code:  4/1ARtbsJpUmCVnQwb42cC3YFWShnDD_FAI6g-JSBQbyW3oCvbx6C1CAt3ad_8



Successfully saved authorization token.


# **Getting the buildings affected by the floods in the government supplied AOI.**

## work

In [65]:
aoi_footprint_path = 'data/syd_reduced_footprint.geojson'
aoi_map_path = 'data/syd_reduced_map.geojson'

In [66]:
aoi_footprint = gpd.read_file(aoi_footprint_path)
aoi_map = gpd.read_file(aoi_map_path)

aoi_floodTrace= aoi_map.groupby('class').get_group('flood-trace')
aoi_footprint['footprint_index'] = aoi_footprint.index

# Finding the affected buildings in the government supplied AOI. 
aoi_intersect = gpd.overlay(aoi_floodTrace, aoi_footprint, how='intersection')


In [157]:
aoi_map['class'].unique()

array(['area_imaged', 'area_imaged-pre-flood', 'cloud', 'cloud-pre-flood',
       'flood-trace', 'water-post-flood', 'water-pre-flood'], dtype=object)

In [68]:
aoi_intersect.explore()

Remaining work of this section is put into the function below. We want to keep the 'incomplete' intersection shapes so we can determine the percentage that was affected by the floods. 

## putting it in a function

In [6]:
# Returns a geodata with the buildings affected in the government supplied AOI.

def get_intersection(aoi_footprintPath: str, aoi_mapPath: str ):
    
    # Reading the files in.
    aoi_footprint = gpd.read_file(aoi_footprintPath)
    aoi_map = gpd.read_file(aoi_mapPath)
    
    aoi_floodTrace= aoi_map.groupby('class').get_group('flood-trace')
    aoi_footprint['footprint_index'] = aoi_footprint.index
    
    # Finding the affected buildings in the government supplied AOI. 
    aoi_intersect = gpd.overlay(aoi_floodTrace, aoi_footprint, how='intersection')
    
    aoi_footprint['footprint_index'] = aoi_footprint.index
    
    intersection = aoi_footprint.loc[aoi_intersect['footprint_index']]
    intersection = intersection.drop(columns= 'footprint_index')

    length = len(intersection)
    
    # Number of affected buildings.
    print(f'There are {length} buildings affected in this AOI')
    
    # Saving the file. 
    intersection.to_file("data/aoi_intersect.geojson", driver='GeoJSON')
    
    return intersection

In [7]:
aoi_footprint_path = 'data/syd_reduced_footprint.geojson'
aoi_map_path = 'data/syd_reduced_map.geojson'

Calling the new function

In [8]:
test_intersection = get_intersection(aoi_footprint_path, aoi_map_path)
test_intersection.head()

There are 399 buildings affected in this AOI


geometry
14713  POLYGON ((150.80703 -32.48325, 150.80711 -32.4...
20010  POLYGON ((150.80881 -32.29166, 150.80882 -32.2...
14697  POLYGON ((150.80611 -32.29109, 150.80614 -32.2...
10710  POLYGON ((150.80792 -32.28899, 150.80807 -32.2...
14729  POLYGON ((150.80753 -32.28908, 150.80757 -32.2...

Checking the percentage of intersection with the floodmap. I don't know what 'EPSG:2264', I'm assuming it's some kind of coordinate system. `to_crs` is converting from the original coordinate system we had (not sure what the name of that one was either) to the new coordinate system. We do this because I couldn't use the `.area` function on the original crs. 

information on crs (coordinate reference system) [here](https://geopandas.org/en/stable/docs/user_guide/projections.html), although I couldn't find anything on the differences between the crs'.

Gonzalo suggest UTM crs, from `ee_download` there is a crs conversion function `ee_download.convert_wgs_to_utm
`

In [123]:
aoi_intersect_new = aoi_intersect['geometry'].to_crs('EPSG:2264')

In [158]:
aoi_intersect_new

0      POLYGON ((-56962266.746 14542203.926, -5696226...
1      POLYGON ((-56828054.246 14576661.287, -5682807...
2      POLYGON ((-56828058.917 14578463.749, -5682804...
3      POLYGON ((-56826353.232 14577727.929, -5682635...
4      POLYGON ((-56826457.093 14577912.594, -5682652...
                             ...                        
394    POLYGON ((-56947261.088 14307395.988, -5694723...
395    POLYGON ((-56947143.001 14307869.951, -5694716...
396    POLYGON ((-56947295.619 14307673.925, -5694729...
397    POLYGON ((-56947290.962 14307263.701, -5694727...
398    POLYGON ((-56947145.472 14303881.603, -5694717...
Name: geometry, Length: 399, dtype: geometry

Strange area sizes. Would probably make sense if I knew what the coordinate system was. 

In [126]:
aoi_intersect_new_area = aoi_intersect_new.area
aoi_intersect_new_area.head()

0     817.851994
1    1372.467842
2      80.902739
3     759.894951
4    3848.434612
dtype: float64

In [127]:
test_intersection_new = test_intersection['geometry'].to_crs('EPSG:2264')

Reset the index so the division is done correctly by the same indices.

Add the area to the df that is being plotted so when we hover over a building affected by the flood, we will see it's area. 

In [129]:
test_intersection_new_area = test_intersection_new.reset_index()['geometry'].area

In [148]:
floodCover = aoi_intersect_new_area/test_intersection_new_area
floodCover

0      0.283155
1      1.000000
2      0.023421
3      0.166624
4      1.000000
         ...   
394    1.000000
395    0.999941
396    1.000000
397    1.000000
398    0.817614
Length: 399, dtype: float64

Note the index does not match the index of 'test_intersect', so we will have to fix that in order to update the df. 

In [146]:
fixed_floodCover = (aoi_intersect_new_area/test_intersection_new_area).set_axis(test_intersection.index)
fixed_floodCover

14713    0.283155
20010    1.000000
14697    0.023421
10710    0.166624
14729    1.000000
           ...   
14056    1.000000
15836    0.999941
18137    1.000000
19351    1.000000
19932    0.817614
Length: 399, dtype: float64

In [149]:
test_intersection['flood_cover'] = fixed_floodCover

In [153]:
test_intersection.explore()

Summary of the flood cover. Should note that some of the buildings were affected by the floods but the flood map is missing a small 'square' that was covering the building. This will reduce the total area covered by the flood on the specific building. 

In [151]:
test_intersection['flood_cover'].describe()

count    399.000000
mean       0.713873
std        0.353040
min        0.000164
25%        0.415656
50%        0.937490
75%        1.000000
max        1.000000
Name: flood_cover, dtype: float64

## plotting

In [ ]:
aoi_map = gpd.read_file(aoi_map_path)
aoi_floodTrace= aoi_map.groupby('class').get_group('flood-trace')

In [10]:
aoi_floodTrace.explore()

In [11]:
test_intersection.explore()

## Plotting with `geemap`

some code taken from `HOWTO_inference_on_image_time_series.ipynb` [seen here](http://trillium.tech/ml4floods/content/ml4ops/HOWTO_inference_on_image_time_series.html)

In [12]:
date_event = datetime.strptime("2022-06-01","%Y-%m-%d").replace(tzinfo=timezone.utc)


def generate_polygon(bbox):
    """
    Generates a list of coordinates: [[x1,y1],[x2,y2],[x3,y3],[x4,y4],[x1,y1]]
    """
    return [[bbox[0],bbox[1]],
             [bbox[2],bbox[1]],
             [bbox[2],bbox[3]],
             [bbox[0],bbox[3]],
             [bbox[0],bbox[1]]]

In [13]:
aoi_floodTrace_bounds = tuple(generate_polygon(aoi_floodTrace['geometry'].total_bounds))

In [42]:
aoi_floodTrace_bounds

([150.73728294074465, -32.75266142017167],
 [151.22428762511254, -32.75266142017167],
 [151.22428762511254, -32.24201674828237],
 [150.73728294074465, -32.24201674828237],
 [150.73728294074465, -32.75266142017167])

In [14]:
Area_of_interestFloodTrace_geojson = {'type': 'Polygon',
 'coordinates': ((aoi_floodTrace_bounds),)}

In [15]:
Area_of_interestFloodTrace_geojson

{'type': 'Polygon',
 'coordinates': (([150.73728294074465, -32.75266142017167],
   [151.22428762511254, -32.75266142017167],
   [151.22428762511254, -32.24201674828237],
   [150.73728294074465, -32.24201674828237],
   [150.73728294074465, -32.75266142017167]),)}

In [16]:
Pol_floodTrace = ee.Geometry(Area_of_interestFloodTrace_geojson)

In [17]:
PolFloodTrace_2_clip = ee.Geometry.Polygon(aoi_floodTrace_bounds)

In [18]:
Permanent_water_img = ee_download.permanent_water_image(date_event.year, PolFloodTrace_2_clip)

In [19]:
type(test_intersection)

geopandas.geodataframe.GeoDataFrame

In [20]:
type(test_intersection['geometry'])

geopandas.geoseries.GeoSeries

In [21]:
fc = geemap.geopandas_to_ee(test_intersection)

In [22]:
fc2 = geemap.geopandas_to_ee(aoi_floodTrace)

In [29]:
Map = geemap.Map()

visualization = {
  "bands": ['waterClass'],
  "min": 0.0,
  "max": 3.0,
  "palette": ['cccccc', 'ffffff', '99d9ea', '0000ff']
}

Map.addLayer(Permanent_water_img, visualization, name="JRC Permanent water")

Map.addLayer(Pol_floodTrace, {"color": 'FF000000'}, "Flood Trace Bounds")
Map.addLayer(fc, {"color": 'FF0000'}, "Intersection")
Map.addLayer(fc2, {"color": '000099'}, "Flood Trace")



# Map.centerObject(Pol_floodTrace, zoom=11)
Map.centerObject(fc, zoom=11)

folium.LayerControl(collapsed=False).add_to(Map)
Map

In [32]:
type(aoi_floodTrace)

geopandas.geodataframe.GeoDataFrame

# Testing percentage of intersection

# end of notebook

TO DO

PERMANENT WATER LAYER

CHECKING ON PROGRESS OF DOWNLOADS 

CHECKING ON PROGRESS OF MAPPING: gonzalo help with tracking the progress?

DM (digital elevation models) for flood depth

mentors mentioned that they previously plotted in plt but will use explore() from now on (beth found it)

key buildings? non-residential buildings may be key buildings? IF there is an option for 'government' buildings affected? 